In [1]:
import pandas as pd

from bs4 import BeautifulSoup

import selenium
from selenium import webdriver
from selenium.webdriver.chrome.options import Options
from selenium.webdriver.common.by import By
from selenium.webdriver.common.keys import Keys
from selenium.webdriver.support.wait import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC
from selenium.webdriver.support.ui import Select
from selenium.common.exceptions import TimeoutException, ElementClickInterceptedException


import requests

import time

In [2]:
chrome_option = Options()
chrome_option.add_experimental_option('detach', True)

driver = webdriver.Chrome(options=chrome_option)
wait = WebDriverWait(driver,10)

urls = [['S24', 'https://search.danawa.com/dsearch.php?query=%EC%82%BC%EC%84%B1%EC%A0%84%EC%9E%90+%EA%B0%A4%EB%9F%AD%EC%8B%9Cs24+256gb%2C+%EC%9E%90%EA%B8%89%EC%A0%9C&originalQuery=%EC%82%BC%EC%84%B1%EC%A0%84%EC%9E%90+%EA%B0%A4%EB%9F%AD%EC%8B%9Cs24+256gb%2C+%EC%9E%90%EA%B8%89%EC%A0%9C&checkedInfo=N&volumeType=allvs&page=1&limit=40&sort=opinionDESC&list=list&boost=true&tab=main&addDelivery=N&coupangMemberSort=N&simpleDescOpen=Y&mode=simple&isInitTireSmartFinder=N&recommendedSort=N&defaultUICategoryCode=122515&defaultPhysicsCategoryCode=224%7C48419%7C48829%7C0&defaultVmTab=8&defaultVaTab=2041&isZeroPrice=Y&quickProductYN=N&priceUnitSort=N&priceUnitSortOrder=A']
       , ['아이폰16', 'https://search.danawa.com/dsearch.php?query=%EC%95%84%EC%9D%B4%ED%8F%B016+%EC%9E%90%EA%B8%89%EC%A0%9C']]

target_item = [urls[0][0], urls[1][0]]


In [3]:
def save_to_df(tmp_scoring, tmp_market, tmp_purchasing_date, tmp_review_title, tmp_review_content):
    global df
    tmp_list = []
    for s, m, d, t, c in zip(tmp_scoring, tmp_market, tmp_purchasing_date, tmp_review_title, tmp_review_content):
        tmp_list.append([s, m, d, t, c])
        
    df = pd.concat([df, pd.DataFrame(data = tmp_list, columns = ['scoring', 'market', 'purchasing_date', 'review_title', 'review_content'])])

    print('df에 저장완료!')
    return df

def click_link(link, idx):
    idx = int(idx)
    global target_item
    driver.get(link)
    tmp = BeautifulSoup(driver.page_source, 'html.parser')
    tmp_title = tmp.select('#blog_content > div.summary_info > div.top_summary > h3 > span')[0]
    if target_item[idx] in tmp_title.text:
        return 1
    
    else:
        print('hmm this is error')
        return 0



# 페이지 리스트 계산
def calc_page_list(review_soup):
    global wait
    page_list = []
    wait.until(
                EC.presence_of_element_located((By.CSS_SELECTOR, '#danawa-prodBlog-companyReview-content-list > div > div > div span'))
    )
    
    page_list.append(review_soup.select('#danawa-prodBlog-companyReview-content-list > div > div > div span')[0].text)
    for i in review_soup.select('#danawa-prodBlog-companyReview-content-list > div > div > div a'):
        page_list.append(i['data-pagenumber'])
    return page_list


# 다음 버튼 유무
def is_click_next_button(page_list) :
    if int(page_list[0]) + 9 == int(page_list[-1]):
        return 1

    else:
        return 0
    
# 해당 페이지 크롤링
def crawling(driver):
    soup = BeautifulSoup(driver.page_source, 'html.parser')
    review_soup = soup.select('#danawa-prodBlog-productOpinion-list-self > div.mall_review > div.area_right')
    scoring = [i.text for i in review_soup[0].select('#danawa-prodBlog-companyReview-content-list div.top_info span.point_type_s span')]
    market = [i['alt'] for i in review_soup[0].select('#danawa-prodBlog-companyReview-content-list div.top_info span.mall img')]
    purchasing_date = [i.text for i in review_soup[0].select('#danawa-prodBlog-companyReview-content-list span.date')]
    review_title = [i.text for i in review_soup[0].select('[id^="danawa-prodBlog-companyReview-content-wrap-"] > div.atc_cont > div.tit_W')]
    review_content = [i.text for i in review_soup[0].select('div.atc')]

    return scoring, market, purchasing_date, review_title, review_content


def repit_page(isTarget): 

    if isTarget == 1:
        try :
            while True:
                time.sleep(2)
                wait.until(
                            EC.presence_of_element_located((By.CSS_SELECTOR, '#danawa-prodBlog-productOpinion-list-self > div.mall_review > div.area_right'))
                )
                review_soup = BeautifulSoup(driver.page_source, 'html.parser').select('#danawa-prodBlog-productOpinion-list-self > div.mall_review > div.area_right')[0]
                
                page_list = calc_page_list(review_soup)
                print(page_list)
                if len(page_list) == 1:
                    print(f'{page_list[0]}페이지 시작합니다~~')
                    tmp_scoring, tmp_market, tmp_purchasing_date, tmp_review_title, tmp_review_content = crawling(driver)
                    save_to_df(tmp_scoring, tmp_market, tmp_purchasing_date, tmp_review_title, tmp_review_content)
                    break
                else:
                    for i in page_list:
                        print(f'{i}페이지 시작합니다.')
                        i = int(i)
                        if i % 10 == 1:
                            tmp_scoring, tmp_market, tmp_purchasing_date, tmp_review_title, tmp_review_content = crawling(driver)
                            save_to_df(tmp_scoring, tmp_market, tmp_purchasing_date, tmp_review_title, tmp_review_content)
                            #df_to_file(df)

                        elif i % 10 >= 2:
                            
                            wait.until(
                                EC.presence_of_element_located((By.CSS_SELECTOR, f'a[data-pagenumber="{i}"]'))
                            )
                            time.sleep(1)
                            driver.find_element(By.CSS_SELECTOR, f'a[data-pagenumber="{i}"]').click()
                            tmp_scoring, tmp_market, tmp_purchasing_date, tmp_review_title, tmp_review_content = crawling(driver)
                            save_to_df(tmp_scoring, tmp_market, tmp_purchasing_date, tmp_review_title, tmp_review_content)
                            #df_to_file(df)

                        elif i % 10 == 0:
                            wait.until(
                                EC.presence_of_element_located((By.CSS_SELECTOR, f'a[data-pagenumber="{i}"]'))
                            )
                            time.sleep(1)
                            driver.find_element(By.CSS_SELECTOR, f'a[data-pagenumber="{i}"]').click()

                            tmp_scoring, tmp_market, tmp_purchasing_date, tmp_review_title, tmp_review_content = crawling(driver)
                            save_to_df(tmp_scoring, tmp_market, tmp_purchasing_date, tmp_review_title, tmp_review_content)
                            #df_to_file(df)
                            
                            wait.until(
                                EC.presence_of_element_located((By.CSS_SELECTOR, '[id^="danawa-pagination-button-next-"] > span'))
                            )
                            driver.find_element(By.CSS_SELECTOR, '[id^="danawa-pagination-button-next-"] > span').click()

                            print('클릭함')
                    
                            print(df.tail(5))
                    
                    if not driver.find_elements(By.CSS_SELECTOR, '[id^="danawa-pagination-button-next-"] > span'):        
                        for i in page_list:
                            print(f'{i}페이지 시작합니다~~')
                            i = int(i)
                            if i % 10 == 1:
                                tmp_scoring, tmp_market, tmp_purchasing_date, tmp_review_title, tmp_review_content = crawling(driver)
                                save_to_df(tmp_scoring, tmp_market, tmp_purchasing_date, tmp_review_title, tmp_review_content)
                                #df_to_file(df)

                            elif i % 10 >= 2:
                                
                                wait.until(
                                    EC.presence_of_element_located((By.CSS_SELECTOR, f'a[data-pagenumber="{i}"]'))
                                )
                                time.sleep(1)
                                driver.find_element(By.CSS_SELECTOR, f'a[data-pagenumber="{i}"]').click()
                                tmp_scoring, tmp_market, tmp_purchasing_date, tmp_review_title, tmp_review_content = crawling(driver)
                                save_to_df(tmp_scoring, tmp_market, tmp_purchasing_date, tmp_review_title, tmp_review_content)
                                #df_to_file(df)
                            print("마지막 페이지 이제 시작합니다.")
                            break           

        except TimeoutException as e:
            print(f'{e}모든 페이지가 끝났습니다.')
    else:
        print('target이 아니라서 크롤링하지 않습니다.')


In [4]:
for url in urls:
    tmp = url
    url = url[-1]
    driver.get(url)

    wait.until(
        EC.presence_of_element_located((By.ID, 'paginationArea'))
    )
    
    # 120개 보기로 바꿈
    Select(driver.find_element(by = By.CSS_SELECTOR, value = '#DetailSearch_Wrapper > div.view_opt > div > select')).select_by_value('120')

    header = {'User-Agent': 'Mozila/5.0 (Windows NT 6.3; Trident/7.0; rv:11.0) like Gecko'}
    res = requests.get(url, headers= header)
    soup = BeautifulSoup(res.text, 'html.parser')
    soup2 = soup.select('#productListArea > div.main_prodlist.main_prodlist_list > ul')
    link_list = []

    print('세부 link_list를 추출합니다. 좀 오래 걸리네요(갤럭시 1~2분, 애플 3~5분)')
    for i in range(0, len(soup2[0].select('a', class_ = 'click_log_prod_review_count'))):
        if soup2[0].select('a', class_ = 'click_log_prod_review_count')[i]['href'] != '#' or soup2[0].select('a', class_ = 'click_log_prod_review_count')[i]['href'] != '':
            link_list.append(soup2[0].select('a', class_ = 'click_log_prod_review_count')[i]['href'])

    # 최종 리스트
    link_list = [link for link in link_list if 'companyReviewYN=Y' in link]

    print(f'''
          ▶ {url}의 세부 link_list는 다음과 같고 하나씩 추출합니다.
          ▶ {len(link_list)}개를 추출합니다.
          ▶ {link_list}
          ''')
    

    for idx, link in enumerate(link_list):
        for i in range(0, 2):
            df = pd.DataFrame(columns = ['scoring', 'market', 'purchasing_date', 'review_title', 'review_content'])
            isTarget = click_link(link, i)
            repit_page(isTarget)
            
            if isTarget == 1:
                df.to_csv(f'danawa_review_{tmp[0]}+{idx}.csv', encoding='utf-8 sig', mode = 'w', index = True, header=True)

            else:
                print('target item이 아니라, csv 저장도 하지 않습니다.')
print('★★★★★★★★★★★★★★★★★')
print('★★★추출 끝!★★★★★★★★')
print('★★★★★★★★★★★★★★★★★')
driver.close()

세부 link_list를 추출합니다. 좀 오래 걸리네요(갤럭시 1~2분, 애플 3~5분)

          ▶ https://search.danawa.com/dsearch.php?query=%EC%82%BC%EC%84%B1%EC%A0%84%EC%9E%90+%EA%B0%A4%EB%9F%AD%EC%8B%9Cs24+256gb%2C+%EC%9E%90%EA%B8%89%EC%A0%9C&originalQuery=%EC%82%BC%EC%84%B1%EC%A0%84%EC%9E%90+%EA%B0%A4%EB%9F%AD%EC%8B%9Cs24+256gb%2C+%EC%9E%90%EA%B8%89%EC%A0%9C&checkedInfo=N&volumeType=allvs&page=1&limit=40&sort=opinionDESC&list=list&boost=true&tab=main&addDelivery=N&coupangMemberSort=N&simpleDescOpen=Y&mode=simple&isInitTireSmartFinder=N&recommendedSort=N&defaultUICategoryCode=122515&defaultPhysicsCategoryCode=224%7C48419%7C48829%7C0&defaultVmTab=8&defaultVaTab=2041&isZeroPrice=Y&quickProductYN=N&priceUnitSort=N&priceUnitSortOrder=A의 세부 link_list는 다음과 같고 하나씩 추출합니다.
          ▶ 5개를 추출합니다.
          ▶ ['https://prod.danawa.com/info/?pcode=29677484&keyword=%EC%82%BC%EC%84%B1%EC%A0%84%EC%9E%90+%EA%B0%A4%EB%9F%AD%EC%8B%9Cs24+256gb%2C+%EC%9E%90%EA%B8%89%EC%A0%9C&cate=122515&bookmark=cm_opinion&companyReviewYN=Y#bookmark_cm

ElementClickInterceptedException: Message: element click intercepted: Element <a href="#" onclick="return false;" class="page_num" id="danawa-pagination-button-page-679ba32b83945" data-pagenumber="...">113</a> is not clickable at point (48, 14). Other element would receive the click: <h2 class="f_tit">...</h2>
  (Session info: chrome=132.0.6834.111)
Stacktrace:
	GetHandleVerifier [0x00007FF7815102F5+28725]
	(No symbol) [0x00007FF781472AE0]
	(No symbol) [0x00007FF78130510A]
	(No symbol) [0x00007FF7813610F8]
	(No symbol) [0x00007FF78135EB42]
	(No symbol) [0x00007FF78135BC51]
	(No symbol) [0x00007FF78135ABB1]
	(No symbol) [0x00007FF78134C6B4]
	(No symbol) [0x00007FF78137FFAA]
	(No symbol) [0x00007FF78134BF86]
	(No symbol) [0x00007FF7813801C0]
	(No symbol) [0x00007FF7813A0181]
	(No symbol) [0x00007FF78137FD53]
	(No symbol) [0x00007FF78134A0E3]
	(No symbol) [0x00007FF78134B471]
	GetHandleVerifier [0x00007FF78183F30D+3366989]
	GetHandleVerifier [0x00007FF7818512F0+3440688]
	GetHandleVerifier

## 쓰레기

In [11]:

review_soup = BeautifulSoup(driver.page_source, 'html.parser').select('#danawa-prodBlog-productOpinion-list-self > div.mall_review > div.area_right')[0]
        
page_list = calc_page_list(review_soup)
print(page_list)
if len(page_list) == 1:
    print(f'{page_list[0]}페이지 시작합니다~~')
    tmp_scoring, tmp_market, tmp_purchasing_date, tmp_review_title, tmp_review_content = crawling(driver)
    save_to_df(tmp_scoring, tmp_market, tmp_purchasing_date, tmp_review_title, tmp_review_content)



['111']
111페이지 시작합니다~~
df에 저장완료!


In [61]:
# url = 'https://search.danawa.com/dsearch.php?query=%EC%95%84%EC%9D%B4%ED%8F%B016+%EC%9E%90%EA%B8%89%EC%A0%9C'
# driver.get(url)

# wait.until(
#     EC.presence_of_element_located((By.ID, 'paginationArea'))
# )

# # 120개 보기로 바꿈
# Select(driver.find_element(by = By.CSS_SELECTOR, value = '#DetailSearch_Wrapper > div.view_opt > div > select')).select_by_value('120')

# header = {'User-Agent': 'Mozila/5.0 (Windows NT 6.3; Trident/7.0; rv:11.0) like Gecko'}
# res = requests.get(url, headers= header)
# soup = BeautifulSoup(res.text, 'html.parser')
# soup2 = soup.select('#productListArea > div.main_prodlist.main_prodlist_list > ul')
# link_list = []

# print('세부 link_list를 추출합니다. 좀 오래 걸리네요(갤럭시 1~2분, 애플 3~5분)')
# for i in range(0, len(soup2[0].select('a', class_ = 'click_log_prod_review_count'))):
#     if soup2[0].select('a', class_ = 'click_log_prod_review_count')[i]['href'] != '#' or soup2[0].select('a', class_ = 'click_log_prod_review_count')[i]['href'] != '':
#         link_list.append(soup2[0].select('a', class_ = 'click_log_prod_review_count')[i]['href'])

# # 최종 리스트
# link_list = [link for link in link_list if 'companyReviewYN=Y' in link]

# print(f'''
#         ▶ {url}의 세부 link_list는 다음과 같고 하나씩 추출합니다.
#         ▶ {len(link_list)}개를 추출합니다.
#         ▶ {link_list}
#         ''')


for idx, link in enumerate(link_list):
    for i in range(0, 2):
        df = pd.DataFrame(columns = ['scoring', 'market', 'purchasing_date', 'review_title', 'review_content'])
        isTarget = click_link(link, i)
        repit_page(isTarget)
        
        if isTarget == 1:
            df.to_csv(f'danawa_review_{tmp[0]}+{idx}.csv', encoding='utf-8 sig', mode = 'w', index = True, header=True)

        else:
            print('target item이 아니라, csv 저장도 하지 않습니다.')
print('★★★★★★★★★★★★★★★★★')
print('★★★추출 끝!★★★★★★★★')
print('★★★★★★★★★★★★★★★★★')
driver.close()

hmm this is error
target이 아니라서 크롤링하지 않습니다.
target item이 아니라, csv 저장도 하지 않습니다.
['1', '2', '3', '4', '5', '6', '7', '8', '9', '10']
1페이지 시작합니다.
df에 저장완료!
2페이지 시작합니다.
df에 저장완료!
3페이지 시작합니다.
df에 저장완료!
4페이지 시작합니다.
df에 저장완료!
5페이지 시작합니다.
df에 저장완료!
6페이지 시작합니다.
df에 저장완료!
7페이지 시작합니다.
df에 저장완료!
8페이지 시작합니다.
df에 저장완료!
9페이지 시작합니다.
df에 저장완료!
10페이지 시작합니다.
df에 저장완료!
클릭함
  scoring market purchasing_date review_title  \
5    100점   11번가     2024.12.11.     \n최고예요\n   
6    100점   11번가     2024.10.04.     \n최고예요\n   
7    100점   11번가     2024.11.13.     \n최고예요\n   
8     80점   11번가     2024.10.11.      \n좋아요\n   
9    100점   11번가     2024.10.16.     \n최고예요\n   

                                     review_content  
5  컬러가 너무 이쁜데...왜 일반 모델만 색상을..ㅠㅠ프로나 맥스도 이쁜 색상을 내줬으면  
6                             너무 예쁜 인디핑크 짱조아용 실물 최고  
7                             아이가 첫 아이폰이라고 정말 좋아하네요  
8  오프 매장에 사러갔는데 불친절하셔서 온라인으로 샀습니다 한 일주일 기다렸는데 잘왔습니다  
9                       배송 예정된 날짜보다 빨리받았어요너무 만족스러워요  
['11', '12', '13', '14', '

KeyboardInterrupt: 

In [62]:
df

scoring  market purchasing_date             review_title  \
0     100점  롯데하이마트     2024.09.21.    \n카메라 컨트롤은 일단 굳이?아이\n   
1      80점  롯데하이마트     2024.09.22.    \n카메라 버튼을 대체 왜 만들었는\n   
2     100점    11번가     2024.09.27.                 \n최고예요\n   
3     100점    11번가     2024.10.11.                 \n최고예요\n   
4      80점    11번가     2024.11.06.                  \n좋아요\n   
..     ...     ...             ...                      ...   
5     100점  롯데하이마트     2024.09.22.  \n배송이 하루 늦은 21일 오후에 완\n   
6     100점  롯데하이마트     2024.09.21.          \n아주 만족합니다 감사\n   
7     100점    11번가     2024.10.23.                 \n최고예요\n   
8     100점    11번가     2024.10.15.                 \n최고예요\n   
9     100점  롯데하이마트     2024.09.23.    \n사전예약으로 빠르게 받아서 좋습\n   

                                       review_content  
0   카메라 컨트롤은 일단 굳이?아이폰은 어차피 아이폰이라서 쓰는거라..평가 할게 없고디...  
1   카메라 버튼을 대체 왜 만들었는지 모를 일이지만 13에서 16으로 바꾸니 가볍기도 ...  
2   4년동안 아이폰12 블랙을 사용했는데 배터리도 빨리 줄어들고 속도도 느려져서 아이폰...  
3   슈팅배송을 처음 접했습니다.저는 ‘면’단위 시골에 사는데, 로켓배송도 직접 배송이 ...  
4   아이폰 성능이야 말해 뭐해요!! 완전 좋음여기저기 알아봐도 자급제는 가격이 똑같더라...  
..                                                ...  
5   배송이 하루 늦은 21일 오후에 완료되었습니다20일 출시라서 학수고대했는데 너무너무...  
6                                         아주 만족합니다 감사  
7                         잘사용중입니다 굿! 오랜만에 핸드폰 바꾸니 좋네용  
8                                    상품과 배송 모두만족 합니다.  
9                                 사전예약으로 빠르게 받아서 좋습니다  

[120 rows x 5 columns]

In [58]:
idx = int(idx)
#global target_item
#driver.get(link)
tmp = BeautifulSoup(driver.page_source, 'html.parser')
tmp_title = tmp.select('#blog_content > div.summary_info > div.top_summary > h3 > span')[0]
#print(tmp_title)
for i in range(0, 2):
    i = int(i)
    if target_item[i] in tmp_title.text:
        print(1)
        
    elif target_item[i] in tmp_title.text:
        print('target item이 아니네요')

    else:
        print('hmm this is error')

hmm this is error
1


In [45]:
0 % 2

0

In [8]:
test = ['https://prod.danawa.com/info/?pcode=65223251&keyword=%EC%95%84%EC%9D%B4%ED%8F%B016+%EC%9E%90%EA%B8%89%EC%A0%9C&cate=122515&bookmark=cm_opinion&companyReviewYN=Y#bookmark_cm_opinion', 'https://prod.danawa.com/info/?pcode=65915975&keyword=%EC%95%84%EC%9D%B4%ED%8F%B016+%EC%9E%90%EA%B8%89%EC%A0%9C&cate=122515&bookmark=cm_opinion&companyReviewYN=Y#bookmark_cm_opinion', 'https://prod.danawa.com/info/?pcode=65915981&keyword=%EC%95%84%EC%9D%B4%ED%8F%B016+%EC%9E%90%EA%B8%89%EC%A0%9C&cate=122515&bookmark=cm_opinion&companyReviewYN=Y#bookmark_cm_opinion', 'https://prod.danawa.com/info/?pcode=65222552&keyword=%EC%95%84%EC%9D%B4%ED%8F%B016+%EC%9E%90%EA%B8%89%EC%A0%9C&cate=122515&bookmark=cm_opinion&companyReviewYN=Y#bookmark_cm_opinion', 'https://prod.danawa.com/info/?pcode=65915990&keyword=%EC%95%84%EC%9D%B4%ED%8F%B016+%EC%9E%90%EA%B8%89%EC%A0%9C&cate=122515&bookmark=cm_opinion&companyReviewYN=Y#bookmark_cm_opinion', 'https://prod.danawa.com/info/?pcode=65919671&keyword=%EC%95%84%EC%9D%B4%ED%8F%B016+%EC%9E%90%EA%B8%89%EC%A0%9C&cate=122515&bookmark=cm_opinion&companyReviewYN=Y#bookmark_cm_opinion', 'https://prod.danawa.com/info/?pcode=65223542&keyword=%EC%95%84%EC%9D%B4%ED%8F%B016+%EC%9E%90%EA%B8%89%EC%A0%9C&cate=122515&bookmark=cm_opinion&companyReviewYN=Y#bookmark_cm_opinion', 'https://prod.danawa.com/info/?pcode=65915945&keyword=%EC%95%84%EC%9D%B4%ED%8F%B016+%EC%9E%90%EA%B8%89%EC%A0%9C&cate=122515&bookmark=cm_opinion&companyReviewYN=Y#bookmark_cm_opinion', 'https://prod.danawa.com/info/?pcode=65915999&keyword=%EC%95%84%EC%9D%B4%ED%8F%B016+%EC%9E%90%EA%B8%89%EC%A0%9C&cate=122515&bookmark=cm_opinion&companyReviewYN=Y#bookmark_cm_opinion', 'https://prod.danawa.com/info/?pcode=65915966&keyword=%EC%95%84%EC%9D%B4%ED%8F%B016+%EC%9E%90%EA%B8%89%EC%A0%9C&cate=122515&bookmark=cm_opinion&companyReviewYN=Y#bookmark_cm_opinion', 'https://prod.danawa.com/info/?pcode=65915921&keyword=%EC%95%84%EC%9D%B4%ED%8F%B016+%EC%9E%90%EA%B8%89%EC%A0%9C&cate=122515&bookmark=cm_opinion&companyReviewYN=Y#bookmark_cm_opinion', 'https://prod.danawa.com/info/?pcode=65223752&keyword=%EC%95%84%EC%9D%B4%ED%8F%B016+%EC%9E%90%EA%B8%89%EC%A0%9C&cate=122515&bookmark=cm_opinion&companyReviewYN=Y#bookmark_cm_opinion', 'https://prod.danawa.com/info/?pcode=65915936&keyword=%EC%95%84%EC%9D%B4%ED%8F%B016+%EC%9E%90%EA%B8%89%EC%A0%9C&cate=122515&bookmark=cm_opinion&companyReviewYN=Y#bookmark_cm_opinion', 'https://prod.danawa.com/info/?pcode=28209935&keyword=%EC%95%84%EC%9D%B4%ED%8F%B016+%EC%9E%90%EA%B8%89%EC%A0%9C&cate=122515&bookmark=cm_opinion&companyReviewYN=Y#bookmark_cm_opinion', 'https://prod.danawa.com/info/?pcode=28210235&keyword=%EC%95%84%EC%9D%B4%ED%8F%B016+%EC%9E%90%EA%B8%89%EC%A0%9C&cate=122515&bookmark=cm_opinion&companyReviewYN=Y#bookmark_cm_opinion', 'https://prod.danawa.com/info/?pcode=28210316&keyword=%EC%95%84%EC%9D%B4%ED%8F%B016+%EC%9E%90%EA%B8%89%EC%A0%9C&cate=122515&bookmark=cm_opinion&companyReviewYN=Y#bookmark_cm_opinion', 'https://prod.danawa.com/info/?pcode=17811749&keyword=%EC%95%84%EC%9D%B4%ED%8F%B016+%EC%9E%90%EA%B8%89%EC%A0%9C&cate=122515&bookmark=cm_opinion&companyReviewYN=Y#bookmark_cm_opinion', 'https://prod.danawa.com/info/?pcode=17816072&keyword=%EC%95%84%EC%9D%B4%ED%8F%B016+%EC%9E%90%EA%B8%89%EC%A0%9C&cate=122515&bookmark=cm_opinion&companyReviewYN=Y#bookmark_cm_opinion', 'https://prod.danawa.com/info/?pcode=28210238&keyword=%EC%95%84%EC%9D%B4%ED%8F%B016+%EC%9E%90%EA%B8%89%EC%A0%9C&cate=122515&bookmark=cm_opinion&companyReviewYN=Y#bookmark_cm_opinion', 'https://prod.danawa.com/info/?pcode=28210298&keyword=%EC%95%84%EC%9D%B4%ED%8F%B016+%EC%9E%90%EA%B8%89%EC%A0%9C&cate=122515&bookmark=cm_opinion&companyReviewYN=Y#bookmark_cm_opinion', 'https://prod.danawa.com/info/?pcode=17816393&keyword=%EC%95%84%EC%9D%B4%ED%8F%B016+%EC%9E%90%EA%B8%89%EC%A0%9C&cate=122515&bookmark=cm_opinion&companyReviewYN=Y#bookmark_cm_opinion', 'https://prod.danawa.com/info/?pcode=28210307&keyword=%EC%95%84%EC%9D%B4%ED%8F%B016+%EC%9E%90%EA%B8%89%EC%A0%9C&cate=122515&bookmark=cm_opinion&companyReviewYN=Y#bookmark_cm_opinion', 'https://prod.danawa.com/info/?pcode=17816720&keyword=%EC%95%84%EC%9D%B4%ED%8F%B016+%EC%9E%90%EA%B8%89%EC%A0%9C&cate=122515&bookmark=cm_opinion&companyReviewYN=Y#bookmark_cm_opinion', 'https://prod.danawa.com/info/?pcode=17814161&keyword=%EC%95%84%EC%9D%B4%ED%8F%B016+%EC%9E%90%EA%B8%89%EC%A0%9C&cate=122515&bookmark=cm_opinion&companyReviewYN=Y#bookmark_cm_opinion', 'https://prod.danawa.com/info/?pcode=17814257&keyword=%EC%95%84%EC%9D%B4%ED%8F%B016+%EC%9E%90%EA%B8%89%EC%A0%9C&cate=122515&bookmark=cm_opinion&companyReviewYN=Y#bookmark_cm_opinion', 'https://prod.danawa.com/info/?pcode=17816651&keyword=%EC%95%84%EC%9D%B4%ED%8F%B016+%EC%9E%90%EA%B8%89%EC%A0%9C&cate=122515&bookmark=cm_opinion&companyReviewYN=Y#bookmark_cm_opinion', 'https://prod.danawa.com/info/?pcode=17814239&keyword=%EC%95%84%EC%9D%B4%ED%8F%B016+%EC%9E%90%EA%B8%89%EC%A0%9C&cate=122515&bookmark=cm_opinion&companyReviewYN=Y#bookmark_cm_opinion', 'https://prod.danawa.com/info/?pcode=17814263&keyword=%EC%95%84%EC%9D%B4%ED%8F%B016+%EC%9E%90%EA%B8%89%EC%A0%9C&cate=122515&bookmark=cm_opinion&companyReviewYN=Y#bookmark_cm_opinion', 'https://prod.danawa.com/info/?pcode=17816411&keyword=%EC%95%84%EC%9D%B4%ED%8F%B016+%EC%9E%90%EA%B8%89%EC%A0%9C&cate=122515&bookmark=cm_opinion&companyReviewYN=Y#bookmark_cm_opinion', 'https://prod.danawa.com/info/?pcode=17816753&keyword=%EC%95%84%EC%9D%B4%ED%8F%B016+%EC%9E%90%EA%B8%89%EC%A0%9C&cate=122515&bookmark=cm_opinion&companyReviewYN=Y#bookmark_cm_opinion', 'https://prod.danawa.com/info/?pcode=19257473&keyword=%EC%95%84%EC%9D%B4%ED%8F%B016+%EC%9E%90%EA%B8%89%EC%A0%9C&cate=122515&bookmark=cm_opinion&companyReviewYN=Y#bookmark_cm_opinion', 'https://prod.danawa.com/info/?pcode=17816738&keyword=%EC%95%84%EC%9D%B4%ED%8F%B016+%EC%9E%90%EA%B8%89%EC%A0%9C&cate=122515&bookmark=cm_opinion&companyReviewYN=Y#bookmark_cm_opinion', 'https://prod.danawa.com/info/?pcode=17814242&keyword=%EC%95%84%EC%9D%B4%ED%8F%B016+%EC%9E%90%EA%B8%89%EC%A0%9C&cate=122515&bookmark=cm_opinion&companyReviewYN=Y#bookmark_cm_opinion', 'https://prod.danawa.com/info/?pcode=17816423&keyword=%EC%95%84%EC%9D%B4%ED%8F%B016+%EC%9E%90%EA%B8%89%EC%A0%9C&cate=122515&bookmark=cm_opinion&companyReviewYN=Y#bookmark_cm_opinion', 'https://prod.danawa.com/info/?pcode=19257392&keyword=%EC%95%84%EC%9D%B4%ED%8F%B016+%EC%9E%90%EA%B8%89%EC%A0%9C&cate=122515&bookmark=cm_opinion&companyReviewYN=Y#bookmark_cm_opinion', 'https://prod.danawa.com/info/?pcode=19257407&keyword=%EC%95%84%EC%9D%B4%ED%8F%B016+%EC%9E%90%EA%B8%89%EC%A0%9C&cate=122515&bookmark=cm_opinion&companyReviewYN=Y#bookmark_cm_opinion']
for i in test:
    print(i)

https://prod.danawa.com/info/?pcode=65223251&keyword=%EC%95%84%EC%9D%B4%ED%8F%B016+%EC%9E%90%EA%B8%89%EC%A0%9C&cate=122515&bookmark=cm_opinion&companyReviewYN=Y#bookmark_cm_opinion
https://prod.danawa.com/info/?pcode=65915975&keyword=%EC%95%84%EC%9D%B4%ED%8F%B016+%EC%9E%90%EA%B8%89%EC%A0%9C&cate=122515&bookmark=cm_opinion&companyReviewYN=Y#bookmark_cm_opinion
https://prod.danawa.com/info/?pcode=65915981&keyword=%EC%95%84%EC%9D%B4%ED%8F%B016+%EC%9E%90%EA%B8%89%EC%A0%9C&cate=122515&bookmark=cm_opinion&companyReviewYN=Y#bookmark_cm_opinion
https://prod.danawa.com/info/?pcode=65222552&keyword=%EC%95%84%EC%9D%B4%ED%8F%B016+%EC%9E%90%EA%B8%89%EC%A0%9C&cate=122515&bookmark=cm_opinion&companyReviewYN=Y#bookmark_cm_opinion
https://prod.danawa.com/info/?pcode=65915990&keyword=%EC%95%84%EC%9D%B4%ED%8F%B016+%EC%9E%90%EA%B8%89%EC%A0%9C&cate=122515&bookmark=cm_opinion&companyReviewYN=Y#bookmark_cm_opinion
https://prod.danawa.com/info/?pcode=65919671&keyword=%EC%95%84%EC%9D%B4%ED%8F%B016+%EC%9E%90%EA

In [32]:
global target_item
driver.get(link_list[-1])
tmp = BeautifulSoup(driver.page_source, 'html.parser')
tmp_title = tmp.select('#blog_content > div.summary_info > div.top_summary > h3 > span')[0]
for target in target_item:
    if target in tmp_title.text:
        print(target)
    # if target in tmp_title:
    #     print(tmp_title)
        # review_soup = BeautifulSoup(driver.page_source, 'html.parser').select('#danawa-prodBlog-productOpinion-list-self > div.mall_review > div.area_right')[0]
        # review_soup
    
    # else:
    #     print('target item이 아니네요')


S24


target item이 아니네요
target이 아니라서 크롤링하지 않습니다.
['1', '2', '3', '4', '5', '6', '7', '8', '9', '10']
1페이지 시작합니다.
df에 저장완료!
2페이지 시작합니다.
df에 저장완료!
3페이지 시작합니다.
df에 저장완료!
4페이지 시작합니다.
df에 저장완료!
5페이지 시작합니다.
df에 저장완료!
6페이지 시작합니다.
df에 저장완료!
7페이지 시작합니다.
df에 저장완료!
8페이지 시작합니다.
df에 저장완료!
9페이지 시작합니다.
df에 저장완료!
10페이지 시작합니다.
df에 저장완료!
클릭함
  scoring  market purchasing_date  \
5     80점  롯데하이마트     2024.07.12.   
6    100점     G마켓     2024.05.24.   
7    100점     G마켓     2024.09.03.   
8    100점    11번가     2024.06.18.   
9    100점    삼성닷컴     2024.06.29.   

                                     review_title  \
5                           \n상품은 잘 아는거지만 하이마트몰\n   
6                               \n너무나도 놀라운 휴대폰!\n   
7                     \n배송 빠르고.. 제품은 넘 깔끔하네요...\n   
8                                        \n최고예요\n   
9  \n배송 빠르고, 디자인 좋고, 가볍고 최고입니다.기존에 쓰던 S21 울트...\n   

                                      review_content  
5  상품은 잘 아는거지만 하이마트몰에서 구매한것이  후회스럽네요..오프라인에서 샀다면 ...  
6  놀라운 ai기능!아이폰처럼 깔끔한 디자인!그러

In [65]:
for i in df[df['review_title']].iterrows():
    if '\u200b' in i:
        print(i)

KeyError: "None of [Index(['\\n모친 폰으로 구매 하였습니다. 모친께 저는 그간 엘지제품과 삼성제...\\n',\n       '\\n 운좋게 이벤트 기간에 정말 합리적인 가격으로 잘 구매했습니다?  손목...\\n',\n       '\\n#삼성전자이벤트참여구매동기 :S21 쓰다 침수되서 바꿨어용.왜 구매 하셨...\\n',\n       '\\n역시 믿고 쓰는 삼성입니다. 같은 삼성제품이라도 삼성닷컴만의 차별화...\\n',\n       '\\n갤럭시 S24 기본형을 샀습니다.이번 디자인은 애플 폰처럼 이쁩니다....\\n',\n       '\\n어머니 폰을 바꿔드리기 위해 갤럭시s24 제품을 자급제로 구입하고...\\n',\n       '\\nA사 제품을 사용하면서 개인적으로 너무너무 불편한것들이 많아...\\n',\n       '\\n폴더폰 초기모델을 3년넘게 쓰고있었는데 이후에 출시되는 폰들...\\n',\n       '\\n#삼성전자 이벤트 참여상품 잘받았습니다. 다른 오픈마켓에서 구매하...\\n',\n       '\\n엘지를 사용하다가 s24를 사용하다보니 속도도 빠르고 검색도 빠르고 ...\\n',\n       ...\n       '\\n빠르게 배송왔습니다. 좋은 조건에 구매할 수 있어서 좋...\\n', '\\n최고예요\\n', '\\n좋아요\\n',\n       '\\n최고예요\\n', '\\n화면이   크니까   사용할  때 편하고   좋아요  ...\\n', '\\n굿\\n',\n       '\\n잘 받았습니다.  ^^\\n', '\\n좋아요\\n', '\\n좋아요\\n', '\\n안전하게 잘 받았습니다\\n'],\n      dtype='object', length=11474)] are in the [columns]"

In [66]:
df.to_csv('test.csv', encoding='cp949')
driver.close()

In [144]:
soup = BeautifulSoup(driver.page_source, 'html.parser')
review_soup = soup.select('#danawa-prodBlog-productOpinion-list-self > div.mall_review > div.area_right')
scoring = [i.text for i in review_soup[0].select('#danawa-prodBlog-companyReview-content-list div.top_info span.point_type_s span')]
market = [i['alt'] for i in review_soup[0].select('#danawa-prodBlog-companyReview-content-list div.top_info span.mall img')]
purchasing_date = [i.text for i in review_soup[0].select('#danawa-prodBlog-companyReview-content-list span.date')]
review_title = [i.text for i in review_soup[0].select('[id^="danawa-prodBlog-companyReview-content-wrap-"] > div.atc_cont > div.tit_W')]
review_content = [i.text for i in review_soup[0].select('div.atc')]
review_title

# print(f'''
      
# {scoring}
# {market}      
# {purchasing_date}
# {review_title}
# {review_content}
# ''')

# tmp_list = []
# tmp_list = [[s, m, d, t, c] for s, m, d, t, c in zip(scoring, market, purchasing_date, review_title, review_content)]



# print(tmp_list)
# pd.DataFrame(tmp_list)


['\n#삼성전자이벤트참여갤럭시 S23 FE 사용 후기최근에 갤럭시 S23 FE를 ...\n',
 '\n갤 s10시리즈만 파손돼도 중고또사고 사고사고사고 몇년을쓰다가, 삼성공식...\n',
 '\n삼성전자 상품평 이벤트 참여해요!!삼성강남센터 직원분께서 알려...\n',
 '\n삼성. 갤럭시스마트폰은 가성비가 정말 좋아요. 특히 제가 구매한 ...\n',
 '\n어머니를 위해 갤럭시 S23 FE를 구매했는데, 정말 유용해요! 화면이 크고 ...\n',
 '\n약 한달간 사용해보니전에 사용하던 A시리즈에 비해 역시나 빠른 ...\n',
 '\n아주 만족합니다\n',
 '\n가족들이 갤럭시만 주로 쓰는데 중딩 아이가 쓰던 플립 액정에 검은선...\n',
 '\n최고예요\n',
 '\n주문날짜  7월21일제일 빨리 받을 수 있는 날이 29일이라, 29일로 신청했...\n']

In [147]:
df

scoring market purchasing_date  \
0     100점   삼성닷컴     2024.07.17.   
1      60점   삼성닷컴     2024.05.17.   
2     100점   삼성닷컴     2024.04.28.   
3      80점   삼성닷컴     2024.05.30.   
4     100점   삼성닷컴     2024.07.25.   
..     ...    ...             ...   
5     100점   삼성닷컴     2024.07.14.   
6     100점   11번가     2024.03.08.   
7     100점     옥션     2024.05.14.   
8     100점    G마켓     2024.05.20.   
9     100점    G마켓     2024.05.22.   

                                         review_title  \
0   \n#삼성전자이벤트참여갤럭시 S23 FE 사용 후기최근에 갤럭시 S23 FE를 ...\n   
1     \n갤 s10시리즈만 파손돼도 중고또사고 사고사고사고 몇년을쓰다가, 삼성공식...\n   
2           \n삼성전자 상품평 이벤트 참여해요!!삼성강남센터 직원분께서 알려...\n   
3         \n삼성. 갤럭시스마트폰은 가성비가 정말 좋아요. 특히 제가 구매한 ...\n   
4   \n어머니를 위해 갤럭시 S23 FE를 구매했는데, 정말 유용해요! 화면이 크고 ....   
..                                                ...   
5                               \n디자인 색상 가격 모두 만족해요\n   
6                                            \n최고예요\n   
7               \n빠르게 보내주시고 정품으로 잘 왔습니다. 처음으로 아이...\n   
8                                         \n잘받았습니다.\n   
9                                         \n아주 좋습니다\n   

                                       review_content  
0   #삼성전자이벤트참여\n갤럭시 S23 FE 사용 후기\n최근에 갤럭시 S23 FE를 ...  
1   갤 s10시리즈만 파손돼도 중고또사고 사고사고사고 몇년을쓰다가, 삼성공식서비스센터에...  
2   삼성전자 상품평 이벤트 참여해요!!삼성강남센터 직원분께서 알려주셔서 삼성닷컴에서 할...  
3   삼성. 갤럭시스마트폰은 가성비가 정말 좋아요. 특히 제가 구매한 S23FE는 합리적...  
4   어머니를 위해 갤럭시 S23 FE를 구매했는데, 정말 유용해요! 화면이 크고 선명해...  
..                                                ...  
5                                   디자인 색상 가격 모두 만족해요  
6   갤8쓰다가 할인가격이 괜찮은것 같아서 구매했습니다. 60만원 중반대면 정말 괜찮은 ...  
7   빠르게 보내주시고 정품으로 잘 왔습니다. 처음으로 아이 새 폰으로 사준건데 너무 좋...  
8   민트색 색상도 이쁘고플레그쉽 못지 않은 성능의 FE!! 너무 100만원이 넘는 고가...  
9         배송 빠르게 잘 받았고 역시 성능도 좋고 아주 싼 가격에 잘 구매한거 같습니다  

[310 rows x 5 columns]

In [ ]:
1. 마지막 페이지(231~239는 크롤링 안됨 이거 조치해야함)
2. 다른 상품 반복할 수 있도록

In [ ]:
def calc_page_list(soup):
    review_soup = soup.select('#danawa-prodBlog-productOpinion-list-self > div.mall_review > div.area_right')
    current_page = review_soup[0].select('#danawa-prodBlog-companyReview-content-list > div > div > div span')[0].text
    page_list = [i['data-pagenumber'] for i in review_soup[0].select('#danawa-prodBlog-companyReview-content-list > div > div > div a')]
    current_page, page_list


def next_button(current_page, page_list) :
    if int(current_page) + 9 == int(page_list[-1]):
        print('yes')

    else:
        print('더 이상 다음 페이지 누를게 없음')

In [ ]:
여기서부터 다시 하기 다음 페이지 못 넘어가는 중
10페이지 하면 어디 저장해놓기 (메모리 관리)

In [29]:
for idx, page in enumerate(tmp_page_list):
    page_number = page['data-pagenumber']
    detail_soup = BeautifulSoup(driver.page_source, 'html.parser')
    print(detail_soup)


<html class="js no-touch" lang="ko" style="" xml:lang="ko" xmlns="http://www.w3.org/1999/xhtml"><head>
<title>삼성전자 갤럭시S23 FE 256GB, 자급제 (자급제 공기계) : 다나와 가격비교</title>
<meta content="text/html; charset=utf-8" http-equiv="Content-Type"/><meta content="IE=Edge" http-equiv="X-UA-Compatible"/><meta content="index,follow" name="Robots"/>
<meta content="[다나와] 삼성전자 갤럭시S23 FE 256GB, 자급제 (자급제 공기계)" name="Title"/>
<meta content="태블릿/모바일/디카,휴대폰/스마트폰,전체보기, 삼성전자 갤럭시S23 FE 256GB, 자급제 (자급제 공기계), 요약정보 : 스마트폰(바형) / 5G / 출시OS: 안드로이드13 / 16.3cm(6.4인치) / D-AMOLED 2X / 2340x1080 / 120Hz / 1450nits / [시스템] / 엑시노스2200 / 8코어 / 램: 8GB / 용량: 256GB / [벤치마크] / AP싱글코어: 1582 / AP멀티코어: 3669 / [네트워크] / 802.11ax(Wi-Fi 6E) / 블루투스v5.3 / 나노+eSIM / [카메라] / 후면:5,000만+1,200만+800만화소 / 전면:1,000만화소 / 8K@24fps / F1.8 / 광학줌: 3배 / 디지털줌: 30배 / [AI] / 쓰기/요약/편집 / AI 이미지 편집 / 실시간 통역 / AI 검색 / [배터리] / USB-C / USB3.2 / 4,500mAh / 최대충전: 25W / 무선:최대15W / [규격] / 방수: IP68 / 가로: 76.5mm / 세로: 158mm / 두께: 8.2mm / 무게: 209g, 갤럭시 S23 시리즈를 계승한 아이코닉한

In [81]:
wait.until(
    EC.presence_of_element_located((By.CSS_SELECTOR, f'div.atc_cont > div.atc'))
).text

'인터넷 구매 후 삼성 스토어에서 물건을 수령하였습니다. 1. 스토어 직원들 너무 친절 합니다. 2. 기계를 잘 모르는데 사용법, 주의점, 향후 AS 받는 방법 모두 아주 친절하게 알려 주셔서 매우 감사합니다. 3. 핸드폰 백업도 장장 4시간이 걸렸지면 100%로 확실하게 해주셨습니다. 4. 앞으로도 삼성 이용에 믿음이 확실해 지네요. - 단, 너무 친철하면 직원분들 스트레스가 높아지는것은 아닌지 걱정이네요. 직원분들의 건강과 복지에 많은 지원 바래요. * S23 FE (자급제). 너무나 많은 곳에서 제품을 리뷰해 주어서 딱히 논 할게 없어요. 프리미엄급은 아니지만 그 언저리의 가성비는 최고라고 생각합니다.'

In [87]:
link_list[0]

'https://prod.danawa.com/info/?pcode=29677484&keyword=%EC%82%BC%EC%84%B1%EC%A0%84%EC%9E%90+%EA%B0%A4%EB%9F%AD%EC%8B%9Cs24+256gb%2C+%EC%9E%90%EA%B8%89%EC%A0%9C&cate=122515&bookmark=cm_opinion&companyReviewYN=Y#bookmark_cm_opinion'

In [93]:
final_review_list = []

def review_crawl(soup):
    wait = WebDriverWait(driver,10)
    wait.until(
    EC.presence_of_element_located((By.CSS_SELECTOR, f'div.atc_cont > div.atc'))
    )
    review_list = [review.text for review in soup.select('div.atc_cont > div.atc')]     

    final_review_list.append(review_list)

    return review_list


def next_page(tmp_current_page, tmp_page_list):
    # 페이지 반복
    for idx, page in enumerate(tmp_page_list):
        page_number = int(tmp_current_page) + 1
        print('추출할 페이지', page_number)
        detail_soup = BeautifulSoup(driver.page_source, 'html.parser')
        print(review_crawl(detail_soup))
        final_review_list.append(review_crawl(detail_soup))
        
        driver.find_element(By.CSS_SELECTOR, f'a[data-pagenumber="{page_number}"]').click()
        time.sleep(3)

        wait = WebDriverWait(driver,10)

        wait.until(
            EC.presence_of_element_located((By.CSS_SELECTOR, f'a[data-pagenumber="{page_number}"]'))
        )
        
        print(page, '여기 완료')
    

# def click_next_button():
#     pass


# try: 
#     for idx, link in enumerate(link_list):
driver.get(link_list[0])
res = requests.get(link_list[0], headers= header)
detail_soup = BeautifulSoup(res.text, 'html.parser')

# 현재 페이지
tmp_current_page = detail_soup.select('#danawa-prodBlog-companyReview-content-list > div > div > div > span')[0].text

# 페이지 리스트
tmp_page_list = detail_soup.select('#danawa-prodBlog-companyReview-content-list > div > div > div > a')

# 세부 페이지 첫번쨰 페이지 크롤링
print('현재 페이지', tmp_current_page)
review_crawl(detail_soup)

next_page(tmp_current_page, tmp_page_list)

#click_next_button


# except TimeoutException as E:
#     res = requests.get(link, headers= header)
#     detail_soup = BeautifulSoup(res.text, 'html.parser')
#     review_crawl(detail_soup)

# except ElementClickInterceptedException as E:
#     print('Error : ElementClickInterceptedException')

final_review_list


현재 페이지 1
추출할 페이지 2
['#삼성전자이벤트참여\n갤럭시 S23 FE 사용 후기\n최근에 갤럭시 S23 FE를 손에 넣었는데요, 정말 만족스러운 스마트폰입니다. 제 경험을 간단하게 공유해볼게요!\n\n디자인\n첫인상부터 마음에 쏙 들었어요. 세련되고 고급스러운 디자인에 얇고 가벼워서 손에 쥐기 편해요. 매트한 후면 덕분에 지문도 잘 안 묻고, 다양한 색상 옵션도 있어서 고르는 재미가 있었답니다.\n\n디스플레이\n6.4인치 AMOLED 디스플레이는 정말 환상적이에요. 색감이 화려하고 선명해서 동영상 볼 때 정말 몰입감이 좋아요. 120Hz 주사율 덕분에 스크롤도 부드럽고 게임할 때도 화면 전환이 매끄러워요.\n\n성능\n최신 칩셋 덕분에 속도도 빠르고, 여러 앱을 동시에 실행해도 전혀 끊김이 없어요. 고사양 게임도 문제없이 돌아가서 게임 좋아하시는 분들께도 추천드려요. 6GB나 8GB RAM 옵션이 있어서 멀티태스킹도 문제없답니다.\n\n카메라\n카메라 성능도 훌륭해요. 5000만 화소 메인 카메라로 선명한 사진을 찍을 수 있고, 초광각 렌즈랑 망원 렌즈도 있어서 다양한 사진을 찍을 수 있어요. 특히 야간 모드가 좋아져서 어두운 곳에서도 예쁜 사진을 찍을 수 있답니다.\n\n배터리\n4500mAh 대용량 배터리 덕분에 하루 종일 사용해도 배터리 걱정이 없어요. 고속 충전이랑 무선 충전도 지원해서 급할 때 빠르게 충전할 수 있어서 정말 편리해요.\n\n소프트웨어\n삼성의 One UI는 직관적이고 사용하기 편리해요. 정기적인 업데이트와 보안 패치로 항상 최신 상태를 유지할 수 있어서 안심이 돼요. 다양한 커스터마이징 옵션과 편리한 기능들이 일상 생활을 더욱 편리하게 만들어줘요.\n\n종합 평가\n갤럭시 S23 FE는 정말 가성비 좋은 스마트폰이에요. 디자인, 디스플레이, 성능, 카메라, 배터리 등 모든 면에서 균형 잡힌 성능을 보여주고, 최신 기술을 경험하고 싶은 분들께 강력히 추천드려요.\n\n#삼성전자이벤트참여', '갤 s10시리즈만 파손돼도 중고또사

TimeoutException: Message: 
Stacktrace:
	GetHandleVerifier [0x00007FF7B18180D5+2992373]
	(No symbol) [0x00007FF7B14ABFD0]
	(No symbol) [0x00007FF7B134590A]
	(No symbol) [0x00007FF7B139926E]
	(No symbol) [0x00007FF7B139955C]
	(No symbol) [0x00007FF7B13E27D7]
	(No symbol) [0x00007FF7B13BF3AF]
	(No symbol) [0x00007FF7B13DF584]
	(No symbol) [0x00007FF7B13BF113]
	(No symbol) [0x00007FF7B138A918]
	(No symbol) [0x00007FF7B138BA81]
	GetHandleVerifier [0x00007FF7B1876A2D+3379789]
	GetHandleVerifier [0x00007FF7B188C32D+3468109]
	GetHandleVerifier [0x00007FF7B1880043+3418211]
	GetHandleVerifier [0x00007FF7B160C78B+847787]
	(No symbol) [0x00007FF7B14B757F]
	(No symbol) [0x00007FF7B14B2FC4]
	(No symbol) [0x00007FF7B14B315D]
	(No symbol) [0x00007FF7B14A2979]
	BaseThreadInitThunk [0x00007FF9268F7374+20]
	RtlUserThreadStart [0x00007FF927C7CC91+33]


In [84]:
final_review_list

[['모친 폰으로 구매 하였습니다. \r\n\r\n모친께 저는 그간 엘지제품과 삼성제품을 2-3년에 한 번씩 바꾸어 사용하도록 했었습니다. 엘지제품이 나오지 않고나서부터는 삼성제품의 폴드3에디션을 사용하시도록 했었습니다.\r\n\r\n에디션이라는 이벤트가 특별했고 화면도 넓고 사진도 잘나온다 소문나 늘 지인분들과의 추억은 모친의 휴대전화에 먼저 저장이 되고는 했었습니다. 그런데 언제부턴가 사진에는 뿌연 현상이 생겼고, 접히는 부분이 눈에 띄게 미워보이기 시작했고 서비스센터에서 교체를 받았음에도 느려짐과 카메라의 불편한 현상은 나아지질 않았죠 거기에 손목이 이제는 아프다는 모친의 말씀을 듣고 플립과 고민을 하다가 \r\n\r\n이번 시리즈 제품을 구매하게 되었습니다. 울트라 사양은 아니더라도 플러스 사양으로 해 드리려던 걸 단순 무게 차이를 위해 일반으로 선택했고, 조금 더 특별함을 느끼실까하여 오렌지 색상으로 선택했습니다. \r\n\r\n무게, 크기, 번역기능, 편집기능, 카메라, 시계연동 관심을 갖고 확인하시던 부분입니다. 그리고 평소 CCTv 앱을 사용하시곤 하는데 실행 할때 폴드 3때보다 그 부분도 원할하게 사용 가능 하시다고 하네요. \r\n데이터를 옮기는 과정도 99% 에서 넘어가지를 않아서 기다리는 시간이 삼십분을 넘겼지만 재실행을 해보고 나니 빠른편은 아니더라도 깔끔한 편이었습니다. \r\n\r\n삼성제품은 유달리 안내서가 꼼꼼하여 천천히 읽어보면 모두가 이해하고 따라 갈 수 있지만 실상 그 안내서를 다 읽기는 버거움은 있습니다. 필요한 부분은 찾기 버튼을 눌러 찾아서 설정기능이 있어 편하기도 했습니다. \r\n\r\n그리고 색달랐던 점은 데이터 넘어오기를 할 때 키보드 설정에 대해서는 시스템설정이 그대로 넘어오지는 않더라구요 예를들어 천지인으로 설정한걸 새 기기에 천지인으로 그대로 설정되지 않는 현상 이 부분은 보안상의 이유로 제외하고 읽어들인걸까요?\r\n\r\n\r\n참고로 부친은 애플제품을 쓰십니다.\r\n부친께 애플제품을 선택하게 해 드린

In [7]:
final_review_list

[['#삼성전자이벤트참여\r\n갤럭시 S23 FE 사용 후기\r\n최근에 갤럭시 S23 FE를 손에 넣었는데요, 정말 만족스러운 스마트폰입니다. 제 경험을 간단하게 공유해볼게요!\r\n\r\n디자인\r\n첫인상부터 마음에 쏙 들었어요. 세련되고 고급스러운 디자인에 얇고 가벼워서 손에 쥐기 편해요. 매트한 후면 덕분에 지문도 잘 안 묻고, 다양한 색상 옵션도 있어서 고르는 재미가 있었답니다.\r\n\r\n디스플레이\r\n6.4인치 AMOLED 디스플레이는 정말 환상적이에요. 색감이 화려하고 선명해서 동영상 볼 때 정말 몰입감이 좋아요. 120Hz 주사율 덕분에 스크롤도 부드럽고 게임할 때도 화면 전환이 매끄러워요.\r\n\r\n성능\r\n최신 칩셋 덕분에 속도도 빠르고, 여러 앱을 동시에 실행해도 전혀 끊김이 없어요. 고사양 게임도 문제없이 돌아가서 게임 좋아하시는 분들께도 추천드려요. 6GB나 8GB RAM 옵션이 있어서 멀티태스킹도 문제없답니다.\r\n\r\n카메라\r\n카메라 성능도 훌륭해요. 5000만 화소 메인 카메라로 선명한 사진을 찍을 수 있고, 초광각 렌즈랑 망원 렌즈도 있어서 다양한 사진을 찍을 수 있어요. 특히 야간 모드가 좋아져서 어두운 곳에서도 예쁜 사진을 찍을 수 있답니다.\r\n\r\n배터리\r\n4500mAh 대용량 배터리 덕분에 하루 종일 사용해도 배터리 걱정이 없어요. 고속 충전이랑 무선 충전도 지원해서 급할 때 빠르게 충전할 수 있어서 정말 편리해요.\r\n\r\n소프트웨어\r\n삼성의 One UI는 직관적이고 사용하기 편리해요. 정기적인 업데이트와 보안 패치로 항상 최신 상태를 유지할 수 있어서 안심이 돼요. 다양한 커스터마이징 옵션과 편리한 기능들이 일상 생활을 더욱 편리하게 만들어줘요.\r\n\r\n종합 평가\r\n갤럭시 S23 FE는 정말 가성비 좋은 스마트폰이에요. 디자인, 디스플레이, 성능, 카메라, 배터리 등 모든 면에서 균형 잡힌 성능을 보여주고, 최신 기술을 경험하고 싶은 분들께 강력히 추천드려요.\r\n\r\n#

In [132]:
for review in detail_soup.select('div.atc_cont > div.atc'):
    print('*****************')
    print(review.text)
    print('*****************')



*****************
#삼성전자이벤트참여
갤럭시 S23 FE 사용 후기
최근에 갤럭시 S23 FE를 손에 넣었는데요, 정말 만족스러운 스마트폰입니다. 제 경험을 간단하게 공유해볼게요!

디자인
첫인상부터 마음에 쏙 들었어요. 세련되고 고급스러운 디자인에 얇고 가벼워서 손에 쥐기 편해요. 매트한 후면 덕분에 지문도 잘 안 묻고, 다양한 색상 옵션도 있어서 고르는 재미가 있었답니다.

디스플레이
6.4인치 AMOLED 디스플레이는 정말 환상적이에요. 색감이 화려하고 선명해서 동영상 볼 때 정말 몰입감이 좋아요. 120Hz 주사율 덕분에 스크롤도 부드럽고 게임할 때도 화면 전환이 매끄러워요.

성능
최신 칩셋 덕분에 속도도 빠르고, 여러 앱을 동시에 실행해도 전혀 끊김이 없어요. 고사양 게임도 문제없이 돌아가서 게임 좋아하시는 분들께도 추천드려요. 6GB나 8GB RAM 옵션이 있어서 멀티태스킹도 문제없답니다.

카메라
카메라 성능도 훌륭해요. 5000만 화소 메인 카메라로 선명한 사진을 찍을 수 있고, 초광각 렌즈랑 망원 렌즈도 있어서 다양한 사진을 찍을 수 있어요. 특히 야간 모드가 좋아져서 어두운 곳에서도 예쁜 사진을 찍을 수 있답니다.

배터리
4500mAh 대용량 배터리 덕분에 하루 종일 사용해도 배터리 걱정이 없어요. 고속 충전이랑 무선 충전도 지원해서 급할 때 빠르게 충전할 수 있어서 정말 편리해요.

소프트웨어
삼성의 One UI는 직관적이고 사용하기 편리해요. 정기적인 업데이트와 보안 패치로 항상 최신 상태를 유지할 수 있어서 안심이 돼요. 다양한 커스터마이징 옵션과 편리한 기능들이 일상 생활을 더욱 편리하게 만들어줘요.

종합 평가
갤럭시 S23 FE는 정말 가성비 좋은 스마트폰이에요. 디자인, 디스플레이, 성능, 카메라, 배터리 등 모든 면에서 균형 잡힌 성능을 보여주고, 최신 기술을 경험하고 싶은 분들께 강력히 추천드려요.

#삼성전자이벤트참여
*****************
*****************
갤 s10시리즈만 파손돼도